# V. Harvey IBM Data Science Specialization Capstone Project Notebook
## Peer-Graded Assignment: Segmenting and Clustering Neighborhoods in Toronto
### Part 3: Segmenting and Clustering Neighborhoods in Toronto

### Import Libraries:

In [2]:
pip install geopy

Note: you may need to restart the kernel to use updated packages.


In [3]:
pip install lxml

Note: you may need to restart the kernel to use updated packages.


In [4]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Libraries imported.


### Read HTML table:
Download Postal codes for city of Toronto, Ontario and save to file df_toronto.csv

url = 'https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M'
df = pd.read_html(url)
df_toronto = df[0]
df_toronto.to_csv('df_toronto.csv')

Using the saved file 'df_toronto.csv':

In [18]:
df_toronto = pd.read_csv('df_toronto.csv')
# dropping column 'Unnamed: 0'
df_toronto.drop(['Unnamed: 0'], inplace = True, axis = 1)
df_toronto

Postal Code           Borough  \
0           M1A      Not assigned   
1           M2A      Not assigned   
2           M3A        North York   
3           M4A        North York   
4           M5A  Downtown Toronto   
5           M6A        North York   
6           M7A  Downtown Toronto   
7           M8A      Not assigned   
8           M9A         Etobicoke   
9           M1B       Scarborough   
10          M2B      Not assigned   
11          M3B        North York   
12          M4B         East York   
13          M5B  Downtown Toronto   
14          M6B        North York   
15          M7B      Not assigned   
16          M8B      Not assigned   
17          M9B         Etobicoke   
18          M1C       Scarborough   
19          M2C      Not assigned   
20          M3C        North York   
21          M4C         East York   
22          M5C  Downtown Toronto   
23          M6C              York   
24          M7C      Not assigned   
25          M8C      Not assigned   
26          M9C         Etobicoke   
27          M1E       Scarborough   
28          M2E      Not assigned   
29          M3E      Not assigned   
30          M4E      East Toronto   
31          M5E  Downtown Toronto   
32          M6E              York   
33          M7E      Not assigned   
34          M8E      Not assigned   
35          M9E      Not assigned   
36          M1G       Scarborough   
37          M2G      Not assigned   
38          M3G      Not assigned   
39          M4G         East York   
40          M5G  Downtown Toronto   
41          M6G  Downtown Toronto   
42          M7G      Not assigned   
43          M8G      Not assigned   
44          M9G      Not assigned   
45          M1H       Scarborough   
46          M2H        North York   
47          M3H        North York   
48          M4H         East York   
49          M5H  Downtown Toronto   
50          M6H      West Toronto   
51          M7H      Not assigned   
52          M8H      Not assigned   
53          M9H      Not assigned   
54          M1J       Scarborough   
55          M2J        North York   
56          M3J        North York   
57          M4J         East York   
58          M5J  Downtown Toronto   
59          M6J      West Toronto   
60          M7J      Not assigned   
61          M8J      Not assigned   
62          M9J      Not assigned   
63          M1K       Scarborough   
64          M2K        North York   
65          M3K        North York   
66          M4K      East Toronto   
67          M5K  Downtown Toronto   
68          M6K      West Toronto   
69          M7K      Not assigned   
70          M8K      Not assigned   
71          M9K      Not assigned   
72          M1L       Scarborough   
73          M2L        North York   
74          M3L        North York   
75          M4L      East Toronto   
76          M5L  Downtown Toronto   
77          M6L        North York   
78          M7L      Not assigned   
79          M8L      Not assigned   
80          M9L        North York   
81          M1M       Scarborough   
82          M2M        North York   
83          M3M        North York   
84          M4M      East Toronto   
85          M5M        North York   
86          M6M              York   
87          M7M      Not assigned   
88          M8M      Not assigned   
89          M9M        North York   
90          M1N       Scarborough   
91          M2N        North York   
92          M3N        North York   
93          M4N   Central Toronto   
94          M5N   Central Toronto   
95          M6N              York   
96          M7N      Not assigned   
97          M8N      Not assigned   
98          M9N              York   
99          M1P       Scarborough   
100         M2P        North York   
101         M3P      Not assigned   
102         M4P   Central Toronto   
103         M5P   Central Toronto   
104         M6P      West Toronto   
105         M7P      Not assigned   
106         M8P      Not assigned   
107     

### Clear all "Not assigned" Boroughs and Reset Indices

In [19]:
df_toronto_indexNames = df_toronto[df_toronto['Borough'] == "Not assigned"].index
df_toronto_clean = df_toronto.drop(df_toronto_indexNames , inplace=False)
df_toronto_clean

Postal Code           Borough  \
2           M3A        North York   
3           M4A        North York   
4           M5A  Downtown Toronto   
5           M6A        North York   
6           M7A  Downtown Toronto   
8           M9A         Etobicoke   
9           M1B       Scarborough   
11          M3B        North York   
12          M4B         East York   
13          M5B  Downtown Toronto   
14          M6B        North York   
17          M9B         Etobicoke   
18          M1C       Scarborough   
20          M3C        North York   
21          M4C         East York   
22          M5C  Downtown Toronto   
23          M6C              York   
26          M9C         Etobicoke   
27          M1E       Scarborough   
30          M4E      East Toronto   
31          M5E  Downtown Toronto   
32          M6E              York   
36          M1G       Scarborough   
39          M4G         East York   
40          M5G  Downtown Toronto   
41          M6G  Downtown Toronto   
45          M1H       Scarborough   
46          M2H        North York   
47          M3H        North York   
48          M4H         East York   
49          M5H  Downtown Toronto   
50          M6H      West Toronto   
54          M1J       Scarborough   
55          M2J        North York   
56          M3J        North York   
57          M4J         East York   
58          M5J  Downtown Toronto   
59          M6J      West Toronto   
63          M1K       Scarborough   
64          M2K        North York   
65          M3K        North York   
66          M4K      East Toronto   
67          M5K  Downtown Toronto   
68          M6K      West Toronto   
72          M1L       Scarborough   
73          M2L        North York   
74          M3L        North York   
75          M4L      East Toronto   
76          M5L  Downtown Toronto   
77          M6L        North York   
80          M9L        North York   
81          M1M       Scarborough   
82          M2M        North York   
83          M3M        North York   
84          M4M      East Toronto   
85          M5M        North York   
86          M6M              York   
89          M9M        North York   
90          M1N       Scarborough   
91          M2N        North York   
92          M3N        North York   
93          M4N   Central Toronto   
94          M5N   Central Toronto   
95          M6N              York   
98          M9N              York   
99          M1P       Scarborough   
100         M2P        North York   
102         M4P   Central Toronto   
103         M5P   Central Toronto   
104         M6P      West Toronto   
107         M9P         Etobicoke   
108         M1R       Scarborough   
109         M2R        North York   
111         M4R   Central Toronto   
112         M5R   Central Toronto   
113         M6R      West Toronto   
114         M7R       Mississauga   
116         M9R         Etobicoke   
117         M1S       Scarborough   
120         M4S   Central Toronto   
121         M5S  Downtown Toronto   
122         M6S      West Toronto   
126         M1T       Scarborough   
129         M4T   Central Toronto   
130         M5T  Downtown Toronto   
135         M1V       Scarborough   
138         M4V   Central Toronto   
139         M5V  Downtown Toronto   
142         M8V         Etobicoke   
143         M9V         Etobicoke   
144         M1W       Scarborough   
147         M4W  Downtown Toronto   
148         M5W  Downtown Toronto   
151         M8W         Etobicoke   
152         M9W         Etobicoke   
153         M1X       Scarborough   
156         M4X  Downtown Toronto   
157         M5X  Downtown Toronto   
160         M8X         Etobicoke   
165         M4Y  Downtown Toronto   
168         M7Y      East Toronto   
169         M8Y         Etobicoke   
178         M8Z         Etobicoke   

                                          Neighborhood  
2                                            Parkwoods  
3                                     Vic

### Setting "Postal Code" as index:

In [20]:
df_toronto_index = df_toronto_clean.set_index("Postal Code")
df_toronto_index

Borough  \
Postal Code                     
M3A                North York   
M4A                North York   
M5A          Downtown Toronto   
M6A                North York   
M7A          Downtown Toronto   
M9A                 Etobicoke   
M1B               Scarborough   
M3B                North York   
M4B                 East York   
M5B          Downtown Toronto   
M6B                North York   
M9B                 Etobicoke   
M1C               Scarborough   
M3C                North York   
M4C                 East York   
M5C          Downtown Toronto   
M6C                      York   
M9C                 Etobicoke   
M1E               Scarborough   
M4E              East Toronto   
M5E          Downtown Toronto   
M6E                      York   
M1G               Scarborough   
M4G                 East York   
M5G          Downtown Toronto   
M6G          Downtown Toronto   
M1H               Scarborough   
M2H                North York   
M3H                North York   
M4H                 East York   
M5H          Downtown Toronto   
M6H              West Toronto   
M1J               Scarborough   
M2J                North York   
M3J                North York   
M4J                 East York   
M5J          Downtown Toronto   
M6J              West Toronto   
M1K               Scarborough   
M2K                North York   
M3K                North York   
M4K              East Toronto   
M5K          Downtown Toronto   
M6K              West Toronto   
M1L               Scarborough   
M2L                North York   
M3L                North York   
M4L              East Toronto   
M5L          Downtown Toronto   
M6L                North York   
M9L                North York   
M1M               Scarborough   
M2M                North York   
M3M                North York   
M4M              East Toronto   
M5M                North York   
M6M                      York   
M9M                North York   
M1N               Scarborough   
M2N                North York   
M3N                North York   
M4N           Central Toronto   
M5N           Central Toronto   
M6N                      York   
M9N                      York   
M1P               Scarborough   
M2P                North York   
M4P           Central Toronto   
M5P           Central Toronto   
M6P              West Toronto   
M9P                 Etobicoke   
M1R               Scarborough   
M2R                North York   
M4R           Central Toronto   
M5R           Central Toronto   
M6R              West Toronto   
M7R               Mississauga   
M9R                 Etobicoke   
M1S               Scarborough   
M4S           Central Toronto   
M5S          Downtown Toronto   
M6S              West Toronto   
M1T               Scarborough   
M4T           Central Toronto   
M5T          Downtown Toronto   
M1V               Scarborough   
M4V           Central Toronto   
M5V          Downtown Toronto   
M8V                 Etobicoke   
M9V                 Etobicoke   
M1W               Scarborough   
M4W          Downtown Toronto   
M5W          Downtown Toronto   
M8W                 Etobicoke   
M9W                 Etobicoke   
M1X               Scarborough   
M4X          Downtown Toronto   
M5X          Downtown Toronto   
M8X                 Etobicoke   
M4Y          Downtown Toronto   
M7Y              East Toronto   
M8Y                 Etobicoke   
M8Z                 Etobicoke   

                                                  Neighborhood  
Postal Code                                                     
M3A                                                  Parkwoods  
M4A                                           Victoria Village  
M5A                                  Regent Park, Harbourfront  
M6A                           Lawrence Manor, Lawrence Heights  
M7A                Queen's Park, Ontario Provincial Government  
M9A                    Islington Avenue, Humber Valley Village  
M1B                                 

### Import Geospatial Data with Latitude and Longitude of Postal Codes:

In [21]:
df_geospatial_data = pd.read_csv("Geospatial_Coordinates.csv", index_col = "Postal Code")

### Add Latitude and Longitude Columns for each Postal Code to Toronto Neighborhood DataFrame:

In [22]:
for item in df_toronto_index.index:
    for item2 in df_geospatial_data.index:
        if item == item2:
            df_toronto_index.loc[item, "Latitude"] = df_geospatial_data.loc[item2]["Latitude"]
            df_toronto_index.loc[item, "Longitude"] = df_geospatial_data.loc[item2]["Longitude"]

### Toronto Neighborhood Dataset with Reset Indicies:

In [23]:
df_toronto_index.reset_index()

Postal Code           Borough  \
0           M3A        North York   
1           M4A        North York   
2           M5A  Downtown Toronto   
3           M6A        North York   
4           M7A  Downtown Toronto   
5           M9A         Etobicoke   
6           M1B       Scarborough   
7           M3B        North York   
8           M4B         East York   
9           M5B  Downtown Toronto   
10          M6B        North York   
11          M9B         Etobicoke   
12          M1C       Scarborough   
13          M3C        North York   
14          M4C         East York   
15          M5C  Downtown Toronto   
16          M6C              York   
17          M9C         Etobicoke   
18          M1E       Scarborough   
19          M4E      East Toronto   
20          M5E  Downtown Toronto   
21          M6E              York   
22          M1G       Scarborough   
23          M4G         East York   
24          M5G  Downtown Toronto   
25          M6G  Downtown Toronto   
26          M1H       Scarborough   
27          M2H        North York   
28          M3H        North York   
29          M4H         East York   
30          M5H  Downtown Toronto   
31          M6H      West Toronto   
32          M1J       Scarborough   
33          M2J        North York   
34          M3J        North York   
35          M4J         East York   
36          M5J  Downtown Toronto   
37          M6J      West Toronto   
38          M1K       Scarborough   
39          M2K        North York   
40          M3K        North York   
41          M4K      East Toronto   
42          M5K  Downtown Toronto   
43          M6K      West Toronto   
44          M1L       Scarborough   
45          M2L        North York   
46          M3L        North York   
47          M4L      East Toronto   
48          M5L  Downtown Toronto   
49          M6L        North York   
50          M9L        North York   
51          M1M       Scarborough   
52          M2M        North York   
53          M3M        North York   
54          M4M      East Toronto   
55          M5M        North York   
56          M6M              York   
57          M9M        North York   
58          M1N       Scarborough   
59          M2N        North York   
60          M3N        North York   
61          M4N   Central Toronto   
62          M5N   Central Toronto   
63          M6N              York   
64          M9N              York   
65          M1P       Scarborough   
66          M2P        North York   
67          M4P   Central Toronto   
68          M5P   Central Toronto   
69          M6P      West Toronto   
70          M9P         Etobicoke   
71          M1R       Scarborough   
72          M2R        North York   
73          M4R   Central Toronto   
74          M5R   Central Toronto   
75          M6R      West Toronto   
76          M7R       Mississauga   
77          M9R         Etobicoke   
78          M1S       Scarborough   
79          M4S   Central Toronto   
80          M5S  Downtown Toronto   
81          M6S      West Toronto   
82          M1T       Scarborough   
83          M4T   Central Toronto   
84          M5T  Downtown Toronto   
85          M1V       Scarborough   
86          M4V   Central Toronto   
87          M5V  Downtown Toronto   
88          M8V         Etobicoke   
89          M9V         Etobicoke   
90          M1W       Scarborough   
91          M4W  Downtown Toronto   
92          M5W  Downtown Toronto   
93          M8W         Etobicoke   
94          M9W         Etobicoke   
95          M1X       Scarborough   
96          M4X  Downtown Toronto   
97          M5X  Downtown Toronto   
98          M8X         Etobicoke   
99          M4Y  Downtown Toronto   
100         M7Y      East Toronto   
101         M8Y         Etobicoke   
102         M8Z         Etobicoke   

                                          Neighborhood   Latitude  Longitude  
0                                            Parkwoods  43.753259 -79.329656

In [24]:
num_boroughs = len(df_toronto_index["Borough"].unique())
print(f"The dataframe has {num_boroughs} boroughs")

The dataframe has 10 boroughs


The dataframe has 10 unique boroughs listed for the city of Toronto.

### Finding the location coordinates for the city of Toronto:

In [25]:
address = 'Toronto, Canada'

geolocator = Nominatim(user_agent="toronto_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Toronto are 43.6534817, -79.3839347.


### Creating maps of Toronto with the Locations of the postal codes indicated:

In [26]:
# create map of Toronto using latitude and longitude values
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, label in zip(df_toronto_index['Latitude'], df_toronto_index['Longitude'], df_toronto_index['Borough']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)  
    
map_toronto

### Splitting Canadian Postal Code Neighborhoods into distinct neighborhoods by Borough:

In [27]:
df_toronto_neighborhood_data = pd.read_csv('Canada_postal_codes_neighborhoods_split.csv')
df_toronto_neighborhood_data

Postal_Code           Borough  \
0           M3A        North York   
1           M4A        North York   
2           M5A  Downtown Toronto   
3           M5A  Downtown Toronto   
4           M6A        North York   
5           M6A        North York   
6           M7A  Downtown Toronto   
7           M7A  Downtown Toronto   
8           M9A         Etobicoke   
9           M9A         Etobicoke   
10          M1B       Scarborough   
11          M1B       Scarborough   
12          M3B        North York   
13          M4B         East York   
14          M4B         East York   
15          M5B  Downtown Toronto   
16          M5B  Downtown Toronto   
17          M6B        North York   
18          M9B         Etobicoke   
19          M9B         Etobicoke   
20          M9B         Etobicoke   
21          M9B         Etobicoke   
22          M9B         Etobicoke   
23          M1C       Scarborough   
24          M1C       Scarborough   
25          M1C       Scarborough   
26          M3C        North York   
27          M4C         East York   
28          M5C  Downtown Toronto   
29          M6C              York   
30          M9C         Etobicoke   
31          M9C         Etobicoke   
32          M9C         Etobicoke   
33          M9C         Etobicoke   
34          M1E       Scarborough   
35          M1E       Scarborough   
36          M1E       Scarborough   
37          M4E      East Toronto   
38          M5E  Downtown Toronto   
39          M6E              York   
40          M1G       Scarborough   
41          M4G         East York   
42          M5G  Downtown Toronto   
43          M6G  Downtown Toronto   
44          M1H       Scarborough   
45          M2H        North York   
46          M3H        North York   
47          M3H        North York   
48          M3H        North York   
49          M4H         East York   
50          M5H  Downtown Toronto   
51          M5H  Downtown Toronto   
52          M5H  Downtown Toronto   
53          M6H      West Toronto   
54          M6H      West Toronto   
55          M1J       Scarborough   
56          M2J        North York   
57          M2J        North York   
58          M2J        North York   
59          M3J        North York   
60          M3J        North York   
61          M4J         East York   
62          M4J         East York   
63          M5J  Downtown Toronto   
64          M5J  Downtown Toronto   
65          M5J  Downtown Toronto   
66          M6J      West Toronto   
67          M6J      West Toronto   
68          M1K       Scarborough   
69          M1K       Scarborough   
70          M1K       Scarborough   
71          M2K        North York   
72          M3K        North York   
73          M4K      East Toronto   
74          M4K      East Toronto   
75          M5K  Downtown Toronto   
76          M5K  Downtown Toronto   
77          M6K      West Toronto   
78          M6K      West Toronto   
79          M6K      West Toronto   
80          M1L       Scarborough   
81          M1L       Scarborough   
82          M1L       Scarborough   
83          M2L        North York   
84          M2L        North York   
85          M3L        North York   
86          M4L      East Toronto   
87          M4L      East Toronto   
88          M5L  Downtown Toronto   
89          M5L  Downtown Toronto   
90          M6L        North York   
91          M6L        North York   
92          M6L        North York   
93          M9L        North York   
94          M1M       Scarborough   
95          M1M       Scarborough   
96          M1M       Scarborough   
97          M2M        North York   
98          M2M        North York   
99          M3M        North York   
100         M4M      East Toronto   
101         M5M        North York   
102         M5M        North York   
103         M6M              York   
104         M6M              York   
105         M6M              York   
106         M9M        North York   
107     

### Using Nominatim to find the Locations for all Neighborhoods in the dataset and saving to file 'Toronto_Neighborhood_location.txt'

In [28]:
no_value = "NA"

outputFile = open("Toronto_Neighborhood_location.txt", "w")
for item in df_toronto_neighborhood_data.Neighborhood:
    try:
        comb_address = f'{item}, Toronto, Canada'
        address = comb_address

        geolocator = Nominatim(user_agent="toronto_explorer")
        location = geolocator.geocode(address)
        latitude = location.latitude
        longitude = location.longitude
        print('The geograpical coordinate of {}, Toronto are {}, {}.'.format(item, latitude, longitude))
        print(item, latitude, longitude, sep = ",", end = "\n",  file = outputFile)
    except AttributeError:
        print('The geograpical coordinate of {}, Toronto are {}, {}.'.format(item, no_value, no_value))
        print(item, no_value, no_value, sep = ",", end = "\n", file = outputFile)

outputFile.close()


The geograpical coordinate of Parkwoods, Toronto are 43.7587999, -79.3201966.
The geograpical coordinate of Victoria Village, Toronto are 43.732658, -79.3111892.
The geograpical coordinate of Regent Park, Toronto are 43.6607056, -79.3604569.
The geograpical coordinate of Harbourfront, Toronto are 43.6400801, -79.3801495.
The geograpical coordinate of Lawrence Manor, Toronto are 43.7220788, -79.4375067.
The geograpical coordinate of Lawrence Heights, Toronto are 43.7227784, -79.4509332.
The geograpical coordinate of Queen's Park, Toronto are 43.659659, -79.3903399.
The geograpical coordinate of Ontario Provincial Government, Toronto are NA, NA.
The geograpical coordinate of Islington Avenue, Toronto are 43.6794838, -79.5389092.
The geograpical coordinate of Humber Valley Village, Toronto are 43.6664717, -79.5243136.
The geograpical coordinate of Malvern, Toronto are 43.8091955, -79.2217008.
The geograpical coordinate of Rouge, Toronto are 43.8049304, -79.1658374.
The geograpical coordin

### Attached the location data generated to Postal Codes and Neighborhood dataset:

In [29]:
df_toronto_neighborhood_data_complete = pd.read_csv('Complete_LocationInfo_Canada_postal_codes_neighborhoods.csv')
df_toronto_neighborhood_data_complete

Postal_Code           Borough  \
0           M3A        North York   
1           M4A        North York   
2           M5A  Downtown Toronto   
3           M5A  Downtown Toronto   
4           M6A        North York   
5           M6A        North York   
6           M7A  Downtown Toronto   
7           M7A  Downtown Toronto   
8           M9A         Etobicoke   
9           M9A         Etobicoke   
10          M1B       Scarborough   
11          M1B       Scarborough   
12          M3B        North York   
13          M4B         East York   
14          M4B         East York   
15          M5B  Downtown Toronto   
16          M5B  Downtown Toronto   
17          M6B        North York   
18          M9B         Etobicoke   
19          M9B         Etobicoke   
20          M9B         Etobicoke   
21          M9B         Etobicoke   
22          M9B         Etobicoke   
23          M1C       Scarborough   
24          M1C       Scarborough   
25          M1C       Scarborough   
26          M3C        North York   
27          M4C         East York   
28          M5C  Downtown Toronto   
29          M6C              York   
30          M9C         Etobicoke   
31          M9C         Etobicoke   
32          M9C         Etobicoke   
33          M9C         Etobicoke   
34          M1E       Scarborough   
35          M1E       Scarborough   
36          M1E       Scarborough   
37          M4E      East Toronto   
38          M5E  Downtown Toronto   
39          M6E              York   
40          M1G       Scarborough   
41          M4G         East York   
42          M5G  Downtown Toronto   
43          M6G  Downtown Toronto   
44          M1H       Scarborough   
45          M2H        North York   
46          M3H        North York   
47          M3H        North York   
48          M3H        North York   
49          M4H         East York   
50          M5H  Downtown Toronto   
51          M5H  Downtown Toronto   
52          M5H  Downtown Toronto   
53          M6H      West Toronto   
54          M6H      West Toronto   
55          M1J       Scarborough   
56          M2J        North York   
57          M2J        North York   
58          M2J        North York   
59          M3J        North York   
60          M3J        North York   
61          M4J         East York   
62          M4J         East York   
63          M5J  Downtown Toronto   
64          M5J  Downtown Toronto   
65          M5J  Downtown Toronto   
66          M6J      West Toronto   
67          M6J      West Toronto   
68          M1K       Scarborough   
69          M1K       Scarborough   
70          M1K       Scarborough   
71          M2K        North York   
72          M3K        North York   
73          M4K      East Toronto   
74          M4K      East Toronto   
75          M5K  Downtown Toronto   
76          M5K  Downtown Toronto   
77          M6K      West Toronto   
78          M6K      West Toronto   
79          M6K      West Toronto   
80          M1L       Scarborough   
81          M1L       Scarborough   
82          M1L       Scarborough   
83          M2L        North York   
84          M2L        North York   
85          M3L        North York   
86          M4L      East Toronto   
87          M4L      East Toronto   
88          M5L  Downtown Toronto   
89          M5L  Downtown Toronto   
90          M6L        North York   
91          M6L        North York   
92          M6L        North York   
93          M9L        North York   
94          M1M       Scarborough   
95          M1M       Scarborough   
96          M1M       Scarborough   
97          M2M        North York   
98          M2M        North York   
99          M3M        North York   
100         M4M      East Toronto   
101         M5M        North York   
102         M5M        North York   
103         M6M              York   
104         M6M              York   
105         M6M              York   
106         M9M        North York   
107     

### Confirming the number of Boroughs

In [30]:
num_boroughs = len(df_toronto_neighborhood_data_complete["Borough"].unique())
print(f"The dataframe has {num_boroughs} boroughs")

The dataframe has 10 boroughs


### Confirming the number of Boroughs and Neighborhoods:

In [31]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(df_toronto_neighborhood_data_complete['Borough'].unique()),
        df_toronto_neighborhood_data_complete.shape[0]
    )
)

The dataframe has 10 boroughs and 218 neighborhoods.


There are 10 boroughs and 218 neighborhoods listed in the postal code dataset.  

geopy did not determine location for 15 indicated neighborhoods as seen above. The location of each of these neighborhoods were researched and replaced for those that were able to be obtained. Those neighborhoods are:

* Humewood-Cedarvale
* Caledonia-Fairbanks
* Keelesdale and Silverthorn (misspelled in the original directory)
* Railway Lands
* Humber Bay Shores
* West Humber-Clairville

Other listed neighborhoods in the original directory are government facilities. These were deleted as they are not strictly neighborhoods. These are:

* Ontario Provincial Government
* Canada Post Gateway Processing Center
* Island Airport
* Stn A PO Boxes
* Business Reply Mail Processing Center
* South Central Letter Processing Plant Toronto

Other locations were undetermined, possibly due to a spelling mistake or they are a part of another neighborhood. These were also deleted:

* Del Ray
* Beaumond Heights
* South of Bloor

Note: Canada Post Gateway Processing Center is the only location that was indicated under the Mississauga borough. With its deletion that borough was also deleted from the list bringing the number of boroughs to 9 and reducing the number of neighborhoods by 9.

In [32]:
df_toronto_revised = pd.read_csv('Complete_LocationInfo_Canada_postal_codes_neighborhoods_REVISED.csv')
df_toronto_revised

Postal_Code           Borough                Neighborhood   Latitude  \
0           M3A        North York                   Parkwoods  43.758800   
1           M4A        North York            Victoria Village  43.732658   
2           M5A  Downtown Toronto                 Regent Park  43.660706   
3           M5A  Downtown Toronto                Harbourfront  43.640080   
4           M6A        North York              Lawrence Manor  43.722079   
5           M6A        North York            Lawrence Heights  43.722778   
6           M7A  Downtown Toronto                Queen's Park  43.659659   
7           M9A         Etobicoke            Islington Avenue  43.679484   
8           M9A         Etobicoke       Humber Valley Village  43.666472   
9           M1B       Scarborough                     Malvern  43.809196   
10          M1B       Scarborough                       Rouge  43.804930   
11          M3B        North York                   Don Mills  43.775347   
12          M4B         East York               Parkview Hill  43.653482   
13          M4B         East York            Woodbine Gardens  43.712078   
14          M5B  Downtown Toronto             Garden District  43.656500   
15          M5B  Downtown Toronto                     Ryerson  43.658469   
16          M6B        North York                   Glencairn  43.708712   
17          M9B         Etobicoke             West Deane Park  43.663199   
18          M9B         Etobicoke            Princess Gardens  43.640466   
19          M9B         Etobicoke                Martin Grove  43.653482   
20          M9B         Etobicoke                   Islington  43.645335   
21          M9B         Etobicoke                  Cloverdale  43.633637   
22          M1C       Scarborough                  Rouge Hill  43.780271   
23          M1C       Scarborough                  Port Union  43.775504   
24          M1C       Scarborough              Highland Creek  43.790117   
25          M3C        North York                   Don Mills  43.775347   
26          M4C         East York            Woodbine Heights  43.699930   
27          M5C  Downtown Toronto              St. James Town  43.669403   
28          M6C              York          Humewood-Cedarvale  43.691111   
29          M9C         Etobicoke                    Eringate  43.662273   
30          M9C         Etobicoke           Bloordale Gardens  43.635317   
31          M9C         Etobicoke           Old Burnhamthorpe  43.639373   
32          M9C         Etobicoke               Markland Wood  43.631239   
33          M1E       Scarborough                   Guildwood  43.755225   
34          M1E       Scarborough                 Morningside  43.782601   
35          M1E       Scarborough                   West Hill  43.768914   
36          M4E      East Toronto                 The Beaches  43.671024   
37          M5E  Downtown Toronto                 Berczy Park  43.647984   
38          M6E              York         Caledonia-Fairbanks  43.695556   
39          M1G       Scarborough                      Woburn  43.759824   
40          M4G         East York                     Leaside  43.704798   
41          M5G  Downtown Toronto          Central Bay Street  43.667342   
42          M6G  Downtown Toronto                    Christie  43.664111   
43          M1H       Scarborough                   Cedarbrae  43.756467   
44          M2H        North York           Hillcrest Village  43.681695   
45          M3H        North York              Bathurst Manor  43.665519   
46          M3H        North York              Wilson Heights  43.740519   
47          M3H        North York             Downsview North  43.749299   
48          M4H         East York            Thorncliffe Park  43.704553   
49          M5H  Downtown Toronto                    Richmond  43.812589   
50          M5H  Downtown Toronto                    Adelaide  43.650486   
51          M5H  Downtown Toronto                   

In [34]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(df_toronto_revised['Borough'].unique()),
        df_toronto_revised.shape[0]
    )
)

The dataframe has 9 boroughs and 209 neighborhoods.


### Defining Foursquare Credentials and Version (note that I have masked these for privacy):

In [ ]:
CLIENT_ID = '  ' # your Foursquare ID
CLIENT_SECRET = ' ' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

### Function for getting the top 100 venues within a radius of 500 meters for each neighborhood:

In [36]:
LIMIT = 100

In [37]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

### Running the function and generating a dataframe called toronto_venues:

In [38]:
toronto_venues = getNearbyVenues(names=df_toronto_revised['Neighborhood'],
                                   latitudes=df_toronto_revised['Latitude'],
                                   longitudes=df_toronto_revised['Longitude']
                                  )

Parkwoods
Victoria Village
Regent Park
Harbourfront
Lawrence Manor
Lawrence Heights
Queen's Park
Islington Avenue
Humber Valley Village
Malvern
Rouge
Don Mills
Parkview Hill
Woodbine Gardens
Garden District
Ryerson
Glencairn
West Deane Park
Princess Gardens
Martin Grove
Islington
Cloverdale
Rouge Hill
Port Union
Highland Creek
Don Mills
Woodbine Heights
St. James Town
Humewood-Cedarvale
Eringate
Bloordale Gardens
Old Burnhamthorpe
Markland Wood
Guildwood
Morningside
West Hill
The Beaches
Berczy Park
Caledonia-Fairbanks
Woburn
Leaside
Central Bay Street
Christie
Cedarbrae
Hillcrest Village
Bathurst Manor
Wilson Heights
Downsview North
Thorncliffe Park
Richmond
Adelaide
King
Dufferin
Dovercourt Village
Scarborough Village
Fairview
Henry Farm
Oriole
Northwood Park
York University
East Toronto
Broadview North
Harbourfront East
Union Station
Toronto Islands
Little Portugal
Trinity
Kennedy Park
Ionview
East Birchmount Park
Bayview Village
Downsview
The Danforth West
Riverdale
Toronto Dominio

### Checking the size of toronto_venues

In [39]:
print(toronto_venues.shape)
toronto_venues.head()

(6268, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Parkwoods                43.7588              -79.320197   
1    Parkwoods                43.7588              -79.320197   
2    Parkwoods                43.7588              -79.320197   
3    Parkwoods                43.7588              -79.320197   
4    Parkwoods                43.7588              -79.320197   

                Venue  Venue Latitude  Venue Longitude        Venue Category  
0     Allwyn's Bakery       43.759840       -79.324719  Caribbean Restaurant  
1                LCBO       43.757774       -79.314257          Liquor Store  
2  Shoppers Drug Mart       43.760857       -79.324961              Pharmacy  
3        Petro-Canada       43.757950       -79.315187           Gas Station  
4         Pizza Pizza       43.760231       -79.325666           Pizza Place

### Checking the number of venues returned for each neighborhood:

In [40]:
toronto_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  \
Neighborhood                                                                
Adelaide                                      100                     100   
Agincourt                                      12                      12   
Agincourt North                                26                      26   
Albion Gardens                                 10                      10   
Alderwood                                       7                       7   
Bathurst Manor                                 67                      67   
Bathurst Quay                                  25                      25   
Bayview Village                                12                      12   
Bedford Park                                    2                       2   
Berczy Park                                   100                     100   
Birch Cliff                                     4                       4   
Bloordale Gardens                               7                       7   
Broadview North                                 9                       9   
Brockton                                       17                      17   
CN Tower                                       59                      59   
Cabbagetown                                    50                      50   
Caledonia-Fairbanks                             9                       9   
Cedarbrae                                      28                      28   
Central Bay Street                            100                     100   
Chinatown                                      69                      69   
Christie                                       57                      57   
Church and Wellesley                           74                      74   
Clairlea                                        9                       9   
Clarks Corners                                  3                       3   
Cliffcrest                                      5                       5   
Cliffside                                       7                       7   
Cliffside West                                  7                       7   
Cloverdale                                     26                      26   
Commerce Court                                100                     100   
Davisville                                     38                      38   
Davisville North                               38                      38   
Deer Park                                      58                      58   
Design Exchange                               100                     100   
Don Mills                                     128                     128   
Dorset Park                                    10                      10   
Dovercourt Village                             10                      10   
Downsview                                      40                      40   
Downsview North                                10                      10   
Dufferin                                       41                      41   
East Birchmount Park                            4                       4   
East Toronto                                    4                       4   
Emery                                           9                       9   
Eringate                                        2                       2   
Exhibition Place                               36                      36   
Fairview                                       82                      82   
First Canadian Place                          100                     100   
Forest Hill North                               4                       4   
Forest Hill Road Park                           7                       7   
Forest Hill SE                                  4                       4   
Forest Hill West                               20                      20   
Garden District         

### Determining how many unique categories can be curated from the returned venues:

In [42]:
print('There are {} unique categories.'.format(len(toronto_venues['Venue Category'].unique())))

There are 334 unique categories.


### Analyze Each Neighborhood

In [43]:
# one hot encoding
toronto_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
toronto_onehot['Neighborhood'] = toronto_venues['Neighborhood'] 

# # move neighborhood column to the first column
# fixed_columns = [toronto_onehot.columns[-114]] + list(toronto_onehot.columns[:-114] + list(toronto_onehot.columns[-115:]))
# toronto_onehot = toronto_onehot[fixed_columns]

toronto_onehot.head()

Accessories Store  Afghan Restaurant  African Restaurant  Airport  \
0                  0                  0                   0        0   
1                  0                  0                   0        0   
2                  0                  0                   0        0   
3                  0                  0                   0        0   
4                  0                  0                   0        0   

   Airport Service  American Restaurant  Animal Shelter  Antique Shop  \
0                0                    0               0             0   
1                0                    0               0             0   
2                0                    0               0             0   
3                0                    0               0             0   
4                0                    0               0             0   

   Aquarium  Art Gallery  Art Museum  Arts & Crafts Store  \
0         0            0           0                    0   
1         0            0           0                    0   
2         0            0           0                    0   
3         0            0           0                    0   
4         0            0           0                    0   

   Arts & Entertainment  Asian Restaurant  Athletics & Sports  \
0                     0                 0                   0   
1                     0                 0                   0   
2                     0                 0                   0   
3                     0                 0                   0   
4                     0                 0                   0   

   Auto Dealership  Auto Workshop  Automotive Shop  BBQ Joint  Bagel Shop  \
0                0              0                0          0           0   
1                0              0                0          0           0   
2                0              0                0          0           0   
3                0              0                0          0           0   
4                0              0                0          0           0   

   Bakery  Bank  Bar  Baseball Field  Baseball Stadium  Basketball Stadium  \
0       0     0    0               0                 0                   0   
1       0     0    0               0                 0                   0   
2       0     0    0               0                 0                   0   
3       0     0    0               0                 0                   0   
4       0     0    0               0                 0                   0   

   Beach  Beach Bar  Bed & Breakfast  Beer Bar  Beer Store  \
0      0          0                0         0           0   
1      0          0                0         0           0   
2      0          0                0         0           0   
3      0          0                0         0           0   
4      0          0                0         0           0   

   Belgian Restaurant  Big Box Store  Bike Shop  Bike Trail  Bistro  \
0                   0              0          0           0       0   
1                   0              0          0           0       0   
2                   0              0          0           0       0   
3                   0              0          0           0       0   
4                   0              0          0           0       0   

   Bookstore  Boutique  Bowling Alley  Brazilian Restaurant  Breakfast Spot  \
0          0         0              0                     0               0   
1          0         0              0                     0               0   
2          0         0              0                     0               0   
3          0         0              0                     0               0   
4          0         0              0                     0               0   

   Brewery  Bridal Shop  Bubble Tea Shop  Building  Burger Joint  \
0        0            0                0         0             0   
1        0            0       

In [45]:
toronto_onehot.shape

(6268, 334)

### Group Rows by Neighborhood by taking the mean of the frequency of occurrence of each category

In [46]:
toronto_grouped = toronto_onehot.groupby('Neighborhood').mean().reset_index()
toronto_grouped

Neighborhood  Accessories Store  Afghan Restaurant  \
0                      Adelaide           0.000000           0.000000   
1                     Agincourt           0.000000           0.000000   
2               Agincourt North           0.000000           0.000000   
3                Albion Gardens           0.000000           0.000000   
4                     Alderwood           0.000000           0.000000   
5                Bathurst Manor           0.000000           0.000000   
6                 Bathurst Quay           0.000000           0.000000   
7               Bayview Village           0.000000           0.000000   
8                  Bedford Park           0.000000           0.000000   
9                   Berczy Park           0.000000           0.000000   
10                  Birch Cliff           0.000000           0.000000   
11            Bloordale Gardens           0.000000           0.000000   
12              Broadview North           0.000000           0.000000   
13                     Brockton           0.000000           0.000000   
14                     CN Tower           0.000000           0.000000   
15                  Cabbagetown           0.000000           0.000000   
16          Caledonia-Fairbanks           0.000000           0.000000   
17                    Cedarbrae           0.000000           0.000000   
18           Central Bay Street           0.000000           0.010000   
19                    Chinatown           0.000000           0.000000   
20                     Christie           0.000000           0.000000   
21         Church and Wellesley           0.000000           0.013514   
22                     Clairlea           0.000000           0.000000   
23               Clarks Corners           0.000000           0.000000   
24                   Cliffcrest           0.000000           0.000000   
25                    Cliffside           0.000000           0.000000   
26               Cliffside West           0.000000           0.000000   
27                   Cloverdale           0.000000           0.000000   
28               Commerce Court           0.000000           0.000000   
29                   Davisville           0.000000           0.000000   
30             Davisville North           0.000000           0.000000   
31                    Deer Park           0.000000           0.000000   
32              Design Exchange           0.000000           0.000000   
33                    Don Mills           0.015625           0.000000   
34                  Dorset Park           0.000000           0.000000   
35           Dovercourt Village           0.000000           0.000000   
36                    Downsview           0.000000           0.000000   
37              Downsview North           0.000000           0.000000   
38                     Dufferin           0.000000           0.000000   
39         East Birchmount Park           0.000000           0.000000   
40                 East Toronto           0.000000           0.000000   
41                        Emery           0.000000           0.000000   
42                     Eringate           0.000000           0.000000   
43             Exhibition Place           0.000000           0.000000   
44                     Fairview           0.000000           0.000000   
45         First Canadian Place           0.000000           0.000000   
46            Forest Hill North           0.000000           0.000000   
47        Forest Hill Road Park           0.000000           0.000000   
48               Forest Hill SE           0.000000           0.000000   
49             Forest Hill West           0.000000           0.000000   
50              Garden District           0.000000           0.000000   
51                    Glencairn           0.000000           0.000000   
52                  Golden Mile           0.016667           0.000000   
53                  Grange Park           0.000000           0.000000   
54  

### Confirm new size

In [47]:
toronto_grouped.shape

(198, 334)

### Print each neighborhood with the top 5 most common venues:

In [48]:
num_top_venues = 5

for hood in toronto_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = toronto_grouped[toronto_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Adelaide----
            venue  freq
0            Café  0.06
1     Coffee Shop  0.06
2             Gym  0.05
3      Restaurant  0.05
4  Clothing Store  0.04


----Agincourt----
                   venue  freq
0     Chinese Restaurant  0.25
1            Coffee Shop  0.08
2   Hong Kong Restaurant  0.08
3  Vietnamese Restaurant  0.08
4             Food Court  0.08


----Agincourt North----
                venue  freq
0                Bank  0.08
1  Chinese Restaurant  0.08
2              Bakery  0.08
3      Clothing Store  0.04
4        Liquor Store  0.04


----Albion Gardens----
            venue  freq
0   Grocery Store   0.2
1  Hardware Store   0.1
2        Pharmacy   0.1
3  Sandwich Place   0.1
4      Beer Store   0.1


----Alderwood----
            venue  freq
0     Pizza Place  0.29
1             Gym  0.14
2             Pub  0.14
3     Coffee Shop  0.14
4  Sandwich Place  0.14


----Bathurst Manor----
               venue  freq
0  Korean Restaurant  0.21
1      Grocery Store  0.06


### Putting each neighborhood with top venues into a pandas dataframe:

In [49]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [50]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = toronto_grouped['Neighborhood']

for ind in np.arange(toronto_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0         Adelaide           Coffee Shop                  Café   
1        Agincourt    Chinese Restaurant      Asian Restaurant   
2  Agincourt North    Chinese Restaurant                  Bank   
3   Albion Gardens         Grocery Store           Pizza Place   
4        Alderwood           Pizza Place                   Gym   

  3rd Most Common Venue 4th Most Common Venue  5th Most Common Venue  \
0            Restaurant                   Gym         Cosmetics Shop   
1            Food Court           Coffee Shop  Vietnamese Restaurant   
2                Bakery    Frozen Yogurt Shop                    Spa   
3        Hardware Store  Fast Food Restaurant             Beer Store   
4        Sandwich Place              Pharmacy                    Pub   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0        Clothing Store   American Restaurant             Gastropub   
1     Korean Restaurant  Hong Kong Restaurant  Cantonese Restaurant   
2        Clothing Store           Coffee Shop        Sandwich Place   
3  Caribbean Restaurant        Sandwich Place   Fried Chicken Joint   
4           Coffee Shop  Fast Food Restaurant     Electronics Store   

  9th Most Common Venue 10th Most Common Venue  
0    Seafood Restaurant     Italian Restaurant  
1         Shopping Mall          Train Station  
2            Restaurant           Liquor Store  
3              Pharmacy           Dessert Shop  
4  Ethiopian Restaurant          Event Service

### Cluster Neighborhoods

Run k-means to cluster the neighborhoods into 9 clusters

In [51]:
# set number of clusters
kclusters = 9

toronto_grouped_clustering = toronto_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([2, 2, 2, 2, 2, 2, 2, 2, 6, 2], dtype=int32)

### Create a new dataframe that includes the cluster and the top 10 venues for each neighborhood

In [53]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

toronto_merged = df_toronto_revised

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
toronto_merged = toronto_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')


toronto_merged.head() # check the last columns!


Postal_Code           Borough      Neighborhood   Latitude  Longitude  \
0         M3A        North York         Parkwoods  43.758800 -79.320197   
1         M4A        North York  Victoria Village  43.732658 -79.311189   
2         M5A  Downtown Toronto       Regent Park  43.660706 -79.360457   
3         M5A  Downtown Toronto      Harbourfront  43.640080 -79.380150   
4         M6A        North York    Lawrence Manor  43.722079 -79.437507   

   Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
0             2.0           Pizza Place        Discount Store   
1             0.0                   Spa              Bus Line   
2             2.0           Coffee Shop       Thai Restaurant   
3             2.0           Coffee Shop                  Café   
4             0.0     Electronics Store                  Bank   

  3rd Most Common Venue 4th Most Common Venue      5th Most Common Venue  \
0           Gas Station         Shopping Mall       Caribbean Restaurant   
1                  Park       Thai Restaurant  Middle Eastern Restaurant   
2            Food Truck                  Park                 Beer Store   
3                 Hotel            Restaurant         Italian Restaurant   
4            Kids Store                  Park            Doctor's Office   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0          Liquor Store    Chinese Restaurant       Laundry Service   
1            Food Truck   Filipino Restaurant         Event Service   
2         Grocery Store            Restaurant  Fast Food Restaurant   
3        Sandwich Place                  Bank    Chinese Restaurant   
4  Ethiopian Restaurant         Event Service           Event Space   

  9th Most Common Venue 10th Most Common Venue  
0                  Bank            Coffee Shop  
1           Event Space     Falafel Restaurant  
2       Auto Dealership      Electronics Store  
3      Sushi Restaurant                  Plaza  
4    Falafel Restaurant         Farmers Market

In [54]:
toronto_merged['Cluster Labels']
# toronto_merged.Cluster_Labels = toronto_merged.Cluster_Labels.astype(int)

0      2.0
1      0.0
2      2.0
3      2.0
4      0.0
5      2.0
6      8.0
7      8.0
8      1.0
9      2.0
10     0.0
11     2.0
12     2.0
13     8.0
14     2.0
15     2.0
16     2.0
17     NaN
18     2.0
19     2.0
20     2.0
21     2.0
22     3.0
23     5.0
24     0.0
25     2.0
26     2.0
27     2.0
28     1.0
29     0.0
30     1.0
31     1.0
32     0.0
33     3.0
34     2.0
35     2.0
36     2.0
37     2.0
38     2.0
39     2.0
40     1.0
41     2.0
42     2.0
43     2.0
44     2.0
45     2.0
46     1.0
47     2.0
48     2.0
49     2.0
50     2.0
51     2.0
52     2.0
53     2.0
54     8.0
55     2.0
56     0.0
57     8.0
58     0.0
59     1.0
60     8.0
61     2.0
62     2.0
63     2.0
64     0.0
65     2.0
66     2.0
67     2.0
68     0.0
69     1.0
70     2.0
71     2.0
72     2.0
73     2.0
74     2.0
75     2.0
76     2.0
77     2.0
78     2.0
79     2.0
80     1.0
81     1.0
82     8.0
83     0.0
84     2.0
85     2.0
86     2.0
87     2.0
88     2.0
89     8.0
90     4.0

### Dropping two rows that have NaN (17 and 173)

In [55]:
toronto_merged = toronto_merged.drop(17)
toronto_merged = toronto_merged.drop(173)

### Transforming from Cluster Labels from float to int

In [56]:
toronto_merged['Cluster Labels'] = toronto_merged['Cluster Labels'].astype(int)

### Visualize the Clusters

In [57]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(toronto_merged['Latitude'], toronto_merged['Longitude'], toronto_merged['Neighborhood'], toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

### Examining Clusters

#### Cluster 1

In [58]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 0, toronto_merged.columns[[2] + list(range(5, toronto_merged.shape[1]))]]

Neighborhood  Cluster Labels      1st Most Common Venue  \
1       Victoria Village               0                        Spa   
4         Lawrence Manor               0          Electronics Store   
10                 Rouge               0       Fast Food Restaurant   
24        Highland Creek               0                IT Services   
29              Eringate               0                       Park   
32         Markland Wood               0             Baseball Field   
56            Henry Farm               0               Tennis Court   
58        Northwood Park               0                       Park   
64       Toronto Islands               0                Music Venue   
68               Ionview               0              Metro Station   
83          Silver Hills               0  Middle Eastern Restaurant   
101  Lawrence Manor East               0          Electronics Store   
121    Forest Hill North               0                 Playground   
126            Westmount               0                Pizza Place   
147              Swansea               0                       Park   
163       Forest Hill SE               0                 Playground   
176           Humbergate               0            Harbor / Marina   
183             Rosedale               0                       Park   
188          Upper Rouge               0       Fast Food Restaurant   
195       Old Mill North               0                       Park   
197       Old Mill South               0                       Park   
198     King's Mill Park               0                       Park   

          2nd Most Common Venue       3rd Most Common Venue  \
1                      Bus Line                        Park   
4                          Bank                  Kids Store   
10                         Park                 Yoga Studio   
24                         Park                    Pharmacy   
29            Electronics Store                 Yoga Studio   
32                  Golf Course                   Piano Bar   
56                       Lawyer                        Park   
58               Baseball Field  Construction & Landscaping   
64              Harbor / Marina                        Park   
68                Deli / Bodega                        Park   
83                         Park           Fish & Chips Shop   
101                        Bank                  Kids Store   
121    Mediterranean Restaurant                        Park   
126                 Gas Station                        Park   
147  Construction & Landscaping                 Social Club   
163    Mediterranean Restaurant                        Park   
176                        Park                Tennis Court   
183                  Playground                      Lawyer   
188                        Park                 Yoga Studio   
195               Metro Station         American Restaurant   
197               Metro Station         American Restaurant   
198               Metro Station         American Restaurant   

    4th Most Common Venue      5th Most Common Venue 6th Most Common Venue  \
1         Thai Restaurant  Middle Eastern Restaurant            Food Truck   
4                    Park            Doctor's Office  Ethiopian Restaurant   
10      Fish & Chips Shop              Event Service           Event Space   
24    Filipino Restaurant       Ethiopian Restaurant         Event Service   
29      Fish & Chips Shop              Event Service           Event Space   
32                   Park        Filipino Restaurant         Event Service   
56             Restaurant          Electronics Store  Ethiopian Restaurant   
58            Yoga Studio          Fish & Chips Shop           Event Space   
64                   Café        Filipino Restaurant         Event Service   
68            Yoga Studio                Fish Market           Event Space   
83          Event Service                Event Space    Falafel Restau

#### Cluster 2

In [59]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 1, toronto_merged.columns[[2] + list(range(5, toronto_merged.shape[1]))]]

Neighborhood  Cluster Labels 1st Most Common Venue  \
8       Humber Valley Village               1                Bakery   
28         Humewood-Cedarvale               1          Hockey Arena   
30          Bloordale Gardens               1     Convenience Store   
31          Old Burnhamthorpe               1               Dog Run   
40                    Leaside               1        Sandwich Place   
46             Wilson Heights               1        Sandwich Place   
59            York University               1                Bakery   
69       East Birchmount Park               1         Grocery Store   
80                   Clairlea               1     Convenience Store   
81                   Oakridge               1        Ice Cream Shop   
91                Upwood Park               1    Mexican Restaurant   
104                 Humberlea               1                Bakery   
124                 High Park               1     Convenience Store   
141          Richview Gardens               1                   Gym   
148            Clarks Corners               1     Convenience Store   
151                Moore Park               1                   Gym   
175               Silverstone               1                  Pool   
187  West Humber - Clairville               1     Indian Restaurant   

    2nd Most Common Venue  3rd Most Common Venue 4th Most Common Venue  \
8            Skating Rink      Convenience Store              Bus Stop   
28      Convenience Store                  Field                 Trail   
30                   Bank           Intersection           Coffee Shop   
31            Gas Station            Flower Shop                  Park   
40      Convenience Store                   Park   Japanese Restaurant   
46          Deli / Bodega            Pizza Place     Convenience Store   
59            Gas Station      Martial Arts Dojo           Fish Market   
69           Intersection            Gas Station            Beer Store   
80     Mexican Restaurant               Pharmacy  Fast Food Restaurant   
81             Restaurant      Convenience Store          Dessert Shop   
91      Convenience Store  Vietnamese Restaurant           Gas Station   
104        Baseball Field      Convenience Store           Gas Station   
124             Pet Store          Metro Station        Shipping Store   
141          Intersection            Yoga Studio           Fish Market   
148  Caribbean Restaurant            Gas Station           Yoga Studio   
151          Tennis Court      Convenience Store           Yoga Studio   
175     Convenience Store          Event Service         Shopping Mall   
187           Music Venue            Yoga Studio           Fish Market   

    5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
8                    Park           Event Space    Falafel Restaurant   
28            Fish Market         Event Service           Event Space   
30             Print Shop        Sandwich Place            Food Court   
31            Yoga Studio     Fish & Chips Shop           Event Space   
40    Filipino Restaurant  Ethiopian Restaurant         Event Service   
46           Intersection            Beer Store    Italian Restaurant   
59            Event Space    Falafel Restaurant        Farmers Market   
69            Yoga Studio           Fish Market    Falafel Restaurant   
80          Grocery Store            Restaurant        Sandwich Place   
81               Bus Stop                  Park           Event Space   
91            Pizza Place     French Restaurant           Fish Market   
104           Fish Market           Event Space    Falafel Restaurant   
124  Gym / Fitness Center                  Café        Mattress Store   
141           Event Space    Falafel Restaurant        Farmers Market   
148     Fish & Chips Shop           Event Space    Falafel Restaurant   
151     Fish & Chips Shop           Event Space    Falafel Restaurant   
175           Yoga 

#### Cluster 3

In [60]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 2, toronto_merged.columns[[2] + list(range(5, toronto_merged.shape[1]))]]

Neighborhood  Cluster Labels      1st Most Common Venue  \
0                     Parkwoods               2                Pizza Place   
2                   Regent Park               2                Coffee Shop   
3                  Harbourfront               2                Coffee Shop   
5              Lawrence Heights               2             Clothing Store   
9                       Malvern               2       Fast Food Restaurant   
11                    Don Mills               2             Clothing Store   
12                Parkview Hill               2             Clothing Store   
14              Garden District               2             Clothing Store   
15                      Ryerson               2                Coffee Shop   
16                    Glencairn               2                 Playground   
18             Princess Gardens               2                Coffee Shop   
19                 Martin Grove               2             Clothing Store   
20                    Islington               2       Fast Food Restaurant   
21                   Cloverdale               2       Fast Food Restaurant   
25                    Don Mills               2             Clothing Store   
26             Woodbine Heights               2               Skating Rink   
27               St. James Town               2                Coffee Shop   
34                  Morningside               2                Coffee Shop   
35                    West Hill               2                Pizza Place   
36                  The Beaches               2                      Beach   
37                  Berczy Park               2                Coffee Shop   
38          Caledonia-Fairbanks               2                     Bakery   
39                       Woburn               2       Fast Food Restaurant   
41           Central Bay Street               2                Coffee Shop   
42                     Christie               2          Korean Restaurant   
43                    Cedarbrae               2       Fast Food Restaurant   
44            Hillcrest Village               2         Italian Restaurant   
45               Bathurst Manor               2          Korean Restaurant   
47              Downsview North               2                Bus Station   
48             Thorncliffe Park               2          Indian Restaurant   
49                     Richmond               2                 Beer Store   
50                     Adelaide               2                Coffee Shop   
51                         King               2                Coffee Shop   
52                     Dufferin               2                        Bar   
53           Dovercourt Village               2                       Café   
55                     Fairview               2             Clothing Store   
61              Broadview North               2                    Theater   
62            Harbourfront East               2                Coffee Shop   
63                Union Station               2                Coffee Shop   
65              Little Portugal               2                        Bar   
66                      Trinity               2                       Café   
67                 Kennedy Park               2       Fast Food Restaurant   
70              Bayview Village               2                       Bank   
71                    Downsview               2                Bus Station   
72            The Danforth West               2                Coffee Shop   
73                    Riverdale               2      Vietnamese Restaurant   
74      Toronto Dominion Centre               2                Coffee Shop   
75              Design Exchange               2                Coffee Shop   
76                     Brockton               2                        Bar   
77             Parkdale Village               2         Tibetan Restaurant   
78             Exhibition Place          

#### Cluster 4

In [61]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 3, toronto_merged.columns[[2] + list(range(5, toronto_merged.shape[1]))]]

Neighborhood  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
22   Rouge Hill               3         Train Station           Yoga Studio   
33    Guildwood               3         Train Station        Baseball Field   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
22     Fish & Chips Shop         Event Service           Event Space   
33      Storage Facility           Yoga Studio     Fish & Chips Shop   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
22    Falafel Restaurant        Farmers Market  Fast Food Restaurant   
33           Event Space    Falafel Restaurant        Farmers Market   

   9th Most Common Venue 10th Most Common Venue  
22                 Field    Filipino Restaurant  
33  Fast Food Restaurant                  Field

#### Cluster 5

In [62]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 4, toronto_merged.columns[[2] + list(range(5, toronto_merged.shape[1]))]]

Neighborhood  Cluster Labels       1st Most Common Venue  \
90   Maple Leaf Park               4                      Bakery   
92     Humber Summit               4                      Bakery   
200       Humber Bay               4  Construction & Landscaping   

          2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
90   Construction & Landscaping      Business Service                  Park   
92   Construction & Landscaping                  Park     Fish & Chips Shop   
200                        Park          Home Service           Yoga Studio   

    5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
90            Fish Market           Event Space    Falafel Restaurant   
92          Event Service           Event Space    Falafel Restaurant   
200     Fish & Chips Shop         Event Service           Event Space   

    8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
90         Farmers Market  Fast Food Restaurant                  Field  
92         Farmers Market  Fast Food Restaurant                  Field  
200    Falafel Restaurant        Farmers Market   Fast Food Restaurant

#### Cluster 6

In [63]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 5, toronto_merged.columns[[2] + list(range(5, toronto_merged.shape[1]))]]

Neighborhood  Cluster Labels 1st Most Common Venue  \
23          Port Union               5                  Park   
138  Kingsview Village               5                  Park   

    2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
23            Yoga Studio     Fish & Chips Shop         Event Service   
138           Yoga Studio     Fish & Chips Shop         Event Service   

    5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
23            Event Space    Falafel Restaurant        Farmers Market   
138           Event Space    Falafel Restaurant        Farmers Market   

    8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
23   Fast Food Restaurant                 Field    Filipino Restaurant  
138  Fast Food Restaurant                 Field    Filipino Restaurant

#### Cluster 7

In [65]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 6, toronto_merged.columns[[2] + list(range(5, toronto_merged.shape[1]))]]

Neighborhood  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
100  Bedford Park               6    Seafood Restaurant             Locksmith   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
100           Yoga Studio   Filipino Restaurant         Event Service   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
100           Event Space    Falafel Restaurant        Farmers Market   

    9th Most Common Venue 10th Most Common Venue  
100  Fast Food Restaurant                  Field

#### Cluster 8

In [66]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 7, toronto_merged.columns[[2] + list(range(5, toronto_merged.shape[1]))]]

Neighborhood  Cluster Labels 1st Most Common Venue  \
158   Steeles East               7            Playground   
174  South Steeles               7            Playground   
181   Steeles West               7            Playground   
199       Sunnylea               7            Playground   

       2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
158  Health & Beauty Service     Fish & Chips Shop         Event Service   
174  Health & Beauty Service     Fish & Chips Shop         Event Service   
181  Health & Beauty Service     Fish & Chips Shop         Event Service   
199            Deli / Bodega           Fish Market         Event Service   

    5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
158           Event Space    Falafel Restaurant        Farmers Market   
174           Event Space    Falafel Restaurant        Farmers Market   
181           Event Space    Falafel Restaurant        Farmers Market   
199           Event Space    Falafel Restaurant        Farmers Market   

    8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
158  Fast Food Restaurant                 Field    Filipino Restaurant  
174  Fast Food Restaurant                 Field    Filipino Restaurant  
181  Fast Food Restaurant                 Field    Filipino Restaurant  
199  Fast Food Restaurant                 Field    Filipino Restaurant

#### Cluster 9

In [67]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 8, toronto_merged.columns[[2] + list(range(5, toronto_merged.shape[1]))]]

Neighborhood  Cluster Labels   1st Most Common Venue  \
6                Queen's Park               8             Coffee Shop   
7            Islington Avenue               8          Sandwich Place   
13           Woodbine Gardens               8                  Bakery   
54        Scarborough Village               8             Coffee Shop   
57                     Oriole               8  Furniture / Home Store   
60               East Toronto               8              Restaurant   
82                 York Mills               8             Coffee Shop   
89                 North Park               8      Chinese Restaurant   
95   Scarborough Village West               8             Coffee Shop   
102              Mount Dennis               8             Pizza Place   
119           York Mills West               8             Coffee Shop   
139              St. Phillips               8             Coffee Shop   
140      Martin Grove Gardens               8             Coffee Shop   
202        The Queensway East               8        Sushi Restaurant   

      2nd Most Common Venue        3rd Most Common Venue  \
6                      Café               Sandwich Place   
7              Food Service                  Coffee Shop   
13              Coffee Shop                         Park   
54     Fast Food Restaurant           Chinese Restaurant   
57              Coffee Shop                Moving Target   
60              Coffee Shop                   Food Court   
82        French Restaurant                          Pub   
89              Coffee Shop            Convenience Store   
95     Fast Food Restaurant           Chinese Restaurant   
102  Furniture / Home Store                  Coffee Shop   
119       French Restaurant                          Pub   
139             Pizza Place                Grocery Store   
140     American Restaurant                     Pharmacy   
202           Garden Center  Eastern European Restaurant   

    4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
6      Italian Restaurant       Bubble Tea Shop       Thai Restaurant   
7           Smoothie Shop           Yoga Studio                 Field   
13           Home Service     Fish & Chips Shop         Event Service   
54               Pharmacy                   Pub                   Gym   
57      Food & Drink Shop         Train Station           Yoga Studio   
60              Juice Bar           Yoga Studio         Event Service   
82          Burrito Place         Metro Station           Bus Station   
89    American Restaurant           Yoga Studio     Fish & Chips Shop   
95               Pharmacy                   Pub                   Gym   
102          Tennis Court         Grocery Store              Bus Line   
119         Burrito Place         Metro Station           Bus Station   
139           Yoga Studio   Filipino Restaurant         Event Service   
140          Liquor Store           Yoga Studio     Fish & Chips Shop   
202           Coffee Shop                   Gym          Food Service   

    7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
6       French Restaurant    Chinese Restaurant   Japanese Restaurant   
7    Ethiopian Restaurant         Event Service           Event Space   
13            Event Space    Falafel Restaurant        Farmers Market   
54          Shopping Mall           Yoga Studio  Ethiopian Restaurant   
57    Filipino Restaurant           Event Space    Falafel Restaurant   
60            Event Space    Falafel Restaurant        Farmers Market   
82       Business Service        Sandwich Place                   Gym   
89            Event Space    Falafel Restaurant        Farmers Market   
95          Shopping Mall           Yoga Studio  Ethiopian Restaurant   
102   Filipino Restaurant         Event Service           Event Space   
119      Business Service        Sandwich Place                   Gym   
139           Event Space    Falafel Restaurant 